In [29]:
import pandas as pd

In [30]:
df = pd.read_csv('/Users/anushakabber/Downloads/donor_segmentation_by_geography_group3/Week3/final_df.csv')

In [ ]:
# Get Zip code and corresponding State Name from Publicly available data
zips_df_2 = pd.read_csv('/Users/anushakabber/Downloads/donor_segmentation_by_geography_group3/Week3/georef-united-states-of-america-zc-point@public.csv', delimiter=";")

In [ ]:
# Fill in State Names
for ind, row in df.iterrows():
  x = zips_df_2[zips_df_2['Zip Code'] == row['Zip.Code']]['Official State Name'].to_list()
  df['State.Province'][ind] = x[0] if x else row['State.Province']

/var/folders/0t/n_m4t1ts19bfj10brfp3vj700000gn/T/ipykernel_5748/613993711.py:3: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  df['State.Province'][ind] = x[0] if x else row['State.Province']
/var/folders/0t/n_m4t1ts19bfj10brfp3vj700000gn/T/i

In [33]:
import pandas as pd

# Assuming 'df' is already loaded as in the provided code

# Calculate Response Time
df['Email.First.Click.Date'] = pd.to_datetime(df['Email.First.Click.Date'])
df['Email.Send.Date.Time'] = pd.to_datetime(df['Email.Send.Date.Time'])
df['Response.Time'] = (df['Email.First.Click.Date'] - df['Email.Send.Date.Time']).dt.total_seconds()

# Calculate Frequency of Donation
df['Donation.Frequency'] = df.groupby('Account.ID')['Largest.Donation.Amount'].transform(lambda x: (x > 0).sum())

# Calculate Total Donation Amount
df['Total.Donation.Amount'] = df.groupby('Account.ID')['Largest.Donation.Amount'].transform('sum')

# Create the clustering DataFrame
clustering_df = df.groupby('Account.ID').agg(
    Avg_Open_Count=('Open.Count', 'mean'),
    Avg_Email_Link_Click_Count=('Email.Link.Click.Count', 'mean'),
    Avg_Response_Time=('Response.Time', 'mean'),
    Donation_Frequency=('Donation.Frequency', 'first'),  # Take the first value since it's the same for each account
    Total_Donation_Amount=('Total.Donation.Amount', 'first') # Take the first value since it's the same for each account
).reset_index()

In [34]:
clustering_df.fillna(0, inplace=True)
clustering_df['Avg_Response_Time'] = clustering_df['Avg_Response_Time'].apply(lambda x: 0 if x < 0 else x)

In [35]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
import matplotlib.pyplot as plt

# Assuming 'clustering_df' is already defined as in the provided code

# Select features (X) and target variable (y)
features = ['Avg_Open_Count', 'Avg_Email_Link_Click_Count', 'Avg_Response_Time', 'Donation_Frequency']
X = clustering_df[features]
y = clustering_df['Total_Donation_Amount']

# Normalize features (important for linear regression)
X_norm = (X - X.min()) / (X.max() - X.min())

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_norm, y, test_size=0.2, random_state=42)

# Create and train the linear regression model
model = LinearRegression()
model.fit(X_train, y_train)

# Make predictions on the test set
y_pred = model.predict(X_test)

# Evaluate the model
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f"Mean Squared Error: {mse}")
print(f"R-squared: {r2}")

Mean Squared Error: 410876.8419879937
R-squared: 0.039473398026524276


In [36]:
# Create a dictionary to store feature weights
feature_weights = dict(zip(features, model.coef_))

# Calculate the sum of absolute weights
total_weight = sum(abs(weight) for weight in feature_weights.values())

# Calculate proportional scores for each feature
proportional_scores = {feature: abs(weight) / total_weight for feature, weight in feature_weights.items()}

# Print the proportional scores
for feature, score in proportional_scores.items():
    print(f"{feature}: {score}")

Avg_Open_Count: 0.31137998719398907
Avg_Email_Link_Click_Count: 0.21965521318431508
Avg_Response_Time: 0.07116105543068804
Donation_Frequency: 0.3978037441910078


In [37]:
proportional_scores['Avg_Response_Time'] = -1*proportional_scores['Avg_Response_Time']

In [38]:
def calculate_donor_score(donor_data):
    score = 0
    for feature, weight in proportional_scores.items():
        score += weight * donor_data[feature]
    return score

# Example usage: calculate scores for all donors
donor_scores = clustering_df.copy()
donor_scores['Donor_Score'] = X_norm.apply(calculate_donor_score, axis=1)

donor_scores

Account.ID  Avg_Open_Count  Avg_Email_Link_Click_Count  \
0              8             1.0                         0.0   
1              9            18.5                         1.5   
2             12             2.0                         1.0   
3             15            15.0                         6.0   
4             18             3.0                         0.0   
...          ...             ...                         ...   
3280        5615             0.0                         0.0   
3281        5844             1.0                         0.0   
3282        5863             1.0                         1.0   
3283        5867             0.0                         0.0   
3284        7099             0.0                         0.0   

      Avg_Response_Time  Donation_Frequency  Total_Donation_Amount  \
0                   0.0                   3                 300.00   
1              949629.5                   4                 100.00   
2             1173475.0                   4                2802.48   
3                   0.0                   3                  90.00   
4                   0.0                   3                 300.00   
...                 ...                 ...                    ...   
3280                0.0                   2                 104.02   
3281                0.0                   2                 206.60   
3282                0.0                   3                 156.03   
3283                0.0                   2                 200.00   
3284                0.0                   1                  51.96   

      Donor_Score  
0        0.199240  
1        0.309986  
2        0.290056  
3        0.368713  
4        0.199916  
...           ...  
3280     0.132601  
3281     0.132939  
3282     0.226697  
3283     0.132601  
3284     0.066301  

[3285 rows x 7 columns]

In [39]:
donor_scores['Donor_Score'] = donor_scores['Donor_Score'] * 100

donor_scores

Account.ID  Avg_Open_Count  Avg_Email_Link_Click_Count  \
0              8             1.0                         0.0   
1              9            18.5                         1.5   
2             12             2.0                         1.0   
3             15            15.0                         6.0   
4             18             3.0                         0.0   
...          ...             ...                         ...   
3280        5615             0.0                         0.0   
3281        5844             1.0                         0.0   
3282        5863             1.0                         1.0   
3283        5867             0.0                         0.0   
3284        7099             0.0                         0.0   

      Avg_Response_Time  Donation_Frequency  Total_Donation_Amount  \
0                   0.0                   3                 300.00   
1              949629.5                   4                 100.00   
2             1173475.0                   4                2802.48   
3                   0.0                   3                  90.00   
4                   0.0                   3                 300.00   
...                 ...                 ...                    ...   
3280                0.0                   2                 104.02   
3281                0.0                   2                 206.60   
3282                0.0                   3                 156.03   
3283                0.0                   2                 200.00   
3284                0.0                   1                  51.96   

      Donor_Score  
0       19.923984  
1       30.998648  
2       29.005604  
3       36.871278  
4       19.991577  
...           ...  
3280    13.260125  
3281    13.293921  
3282    22.669674  
3283    13.260125  
3284     6.630062  

[3285 rows x 7 columns]

In [ ]:
# 13 is 50th percentile 
donor_scores['Engagement Type'] = donor_scores['Donor_Score'].apply(lambda x: "High Engagement" if x > 13 else "Low Engagement")

donor_scores

Account.ID  Avg_Open_Count  Avg_Email_Link_Click_Count  \
0              8             1.0                         0.0   
1              9            18.5                         1.5   
2             12             2.0                         1.0   
3             15            15.0                         6.0   
4             18             3.0                         0.0   
...          ...             ...                         ...   
3280        5615             0.0                         0.0   
3281        5844             1.0                         0.0   
3282        5863             1.0                         1.0   
3283        5867             0.0                         0.0   
3284        7099             0.0                         0.0   

      Avg_Response_Time  Donation_Frequency  Total_Donation_Amount  \
0                   0.0                   3                 300.00   
1              949629.5                   4                 100.00   
2             1173475.0                   4                2802.48   
3                   0.0                   3                  90.00   
4                   0.0                   3                 300.00   
...                 ...                 ...                    ...   
3280                0.0                   2                 104.02   
3281                0.0                   2                 206.60   
3282                0.0                   3                 156.03   
3283                0.0                   2                 200.00   
3284                0.0                   1                  51.96   

      Donor_Score  Engagement Type  
0       19.923984  High Engagement  
1       30.998648  High Engagement  
2       29.005604  High Engagement  
3       36.871278  High Engagement  
4       19.991577  High Engagement  
...           ...              ...  
3280    13.260125  High Engagement  
3281    13.293921  High Engagement  
3282    22.669674  High Engagement  
3283    13.260125  High Engagement  
3284     6.630062   Low Engagement  

[3285 rows x 8 columns]

In [ ]:
# 75 is 50th percentile
donor_scores['Donation Type'] = donor_scores['Total_Donation_Amount'].apply(lambda x: "High Donation" if x > 75 else "Low Donation")

donor_scores

Account.ID  Avg_Open_Count  Avg_Email_Link_Click_Count  \
0              8             1.0                         0.0   
1              9            18.5                         1.5   
2             12             2.0                         1.0   
3             15            15.0                         6.0   
4             18             3.0                         0.0   
...          ...             ...                         ...   
3280        5615             0.0                         0.0   
3281        5844             1.0                         0.0   
3282        5863             1.0                         1.0   
3283        5867             0.0                         0.0   
3284        7099             0.0                         0.0   

      Avg_Response_Time  Donation_Frequency  Total_Donation_Amount  \
0                   0.0                   3                 300.00   
1              949629.5                   4                 100.00   
2             1173475.0                   4                2802.48   
3                   0.0                   3                  90.00   
4                   0.0                   3                 300.00   
...                 ...                 ...                    ...   
3280                0.0                   2                 104.02   
3281                0.0                   2                 206.60   
3282                0.0                   3                 156.03   
3283                0.0                   2                 200.00   
3284                0.0                   1                  51.96   

      Donor_Score  Engagement Type  Donation Type  
0       19.923984  High Engagement  High Donation  
1       30.998648  High Engagement  High Donation  
2       29.005604  High Engagement  High Donation  
3       36.871278  High Engagement  High Donation  
4       19.991577  High Engagement  High Donation  
...           ...              ...            ...  
3280    13.260125  High Engagement  High Donation  
3281    13.293921  High Engagement  High Donation  
3282    22.669674  High Engagement  High Donation  
3283    13.260125  High Engagement  High Donation  
3284     6.630062   Low Engagement   Low Donation  

[3285 rows x 9 columns]

In [42]:
zip_codes_df = df[['Account.ID', 'State.Province', 'Zip.Code']]
zip_codes_df.drop_duplicates(inplace=True)
merged_df = pd.merge(donor_scores, zip_codes_df[['Account.ID', 'State.Province', 'Zip.Code']], on='Account.ID', how='left')

merged_df

/var/folders/0t/n_m4t1ts19bfj10brfp3vj700000gn/T/ipykernel_5748/56851142.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  zip_codes_df.drop_duplicates(inplace=True)


Account.ID  Avg_Open_Count  Avg_Email_Link_Click_Count  \
0              8             1.0                         0.0   
1              9            18.5                         1.5   
2             12             2.0                         1.0   
3             15            15.0                         6.0   
4             18             3.0                         0.0   
...          ...             ...                         ...   
3280        5615             0.0                         0.0   
3281        5844             1.0                         0.0   
3282        5863             1.0                         1.0   
3283        5867             0.0                         0.0   
3284        7099             0.0                         0.0   

      Avg_Response_Time  Donation_Frequency  Total_Donation_Amount  \
0                   0.0                   3                 300.00   
1              949629.5                   4                 100.00   
2             1173475.0                   4                2802.48   
3                   0.0                   3                  90.00   
4                   0.0                   3                 300.00   
...                 ...                 ...                    ...   
3280                0.0                   2                 104.02   
3281                0.0                   2                 206.60   
3282                0.0                   3                 156.03   
3283                0.0                   2                 200.00   
3284                0.0                   1                  51.96   

      Donor_Score  Engagement Type  Donation Type State.Province  Zip.Code  
0       19.923984  High Engagement  High Donation      Wisconsin     53538  
1       30.998648  High Engagement  High Donation      Wisconsin     53578  
2       29.005604  High Engagement  High Donation      Wisconsin     53558  
3       36.871278  High Engagement  High Donation      Wisconsin     53527  
4       19.991577  High Engagement  High Donation      Wisconsin     53529  
...           ...              ...            ...            ...       ...  
3280    13.260125  High Engagement  High Donation      Wisconsin     53719  
3281    13.293921  High Engagement  High Donation             WI     53232  
3282    22.669674  High Engagement  High Donation      Wisconsin     53593  
3283    13.260125  High Engagement  High Donation     Washington     98112  
3284     6.630062   Low Engagement   Low Donation      Wisconsin     53719  

[3285 rows x 11 columns]

In [43]:
donor_scoring_df = merged_df[['Account.ID', 'Avg_Open_Count',
 'Avg_Email_Link_Click_Count',
 'Avg_Response_Time',
 'Donation_Frequency',
 'Total_Donation_Amount', 'Donor_Score',
 'Engagement Type',
 'Donation Type',
 'State.Province',
 'Zip.Code']]

In [44]:
donor_scoring_df.to_csv('donor_scoring_df.csv', index=False)

In [45]:
merged_df = pd.merge(df, donor_scoring_df[['Account.ID', 'Donor_Score', 'Engagement Type', 'Donation Type']], on='Account.ID', how='left')

merged_df

Unnamed: 0  Account.ID Email.First.Open.Date Email.Last.Open.Date  \
0              0           8                   NaN                  NaN   
1              1           8                   NaN                  NaN   
2              2           8            2022-08-18           2022-08-18   
3              3           9            2021-05-03           2021-06-01   
4              4           9                   NaN                  NaN   
...          ...         ...                   ...                  ...   
5667        5696        5863                   NaN                  NaN   
5668        5697        5863                   NaN                  NaN   
5669        5698        5867                   NaN                  NaN   
5670        5699        5867                   NaN                  NaN   
5671        5700        7099                   NaN                  NaN   

      Open.Count Email.Recipient.Full.Name                  Email  \
0            NaN            Peggy Stebbins   tyandpeggy@gmail.com   
1            NaN            Peggy Stebbins   tyandpeggy@gmail.com   
2            1.0            Peggy Stebbins   tyandpeggy@gmail.com   
3           26.0            Samantha Maier  Sglass32085@gmail.com   
4            NaN            Samantha Maier  Sglass32085@gmail.com   
...          ...                       ...                    ...   
5667         NaN                 Caleb Cox    cjcox.byu@gmail.com   
5668         NaN                 Caleb Cox    cjcox.byu@gmail.com   
5669         NaN    Ken and Lnn Cunningham           ken@kwc1.net   
5670         NaN   Ken and Lynn Cunningham           ken@kwc1.net   
5671         NaN              Julie Wilson       office@umcmh.org   

      Email.Retry.Count Email.Send.Date.Time      Email.Type  ...  \
0                   2.0  2020-09-23 08:15:52  Campaign Email  ...   
1                   2.0  2021-05-03 10:02:19  Campaign Email  ...   
2                   NaN  2022-08-18 06:30:54  Campaign Email  ...   
3                   2.0  2021-05-03 10:02:07  Campaign Email  ...   
4                   2.0  2020-09-23 08:15:45  Campaign Email  ...   
...                 ...                  ...             ...  ...   
5667                2.0  2021-05-03 10:02:37  Campaign Email  ...   
5668                2.0  2020-09-23 08:15:53  Campaign Email  ...   
5669                2.0  2021-05-03 10:03:04  Campaign Email  ...   
5670                NaN  2022-08-18 06:31:00  Campaign Email  ...   
5671                NaN  2022-08-18 06:30:54  Campaign Email  ...   

                City State.Province  Zip.Code Largest.Donation.Amount  \
0                NaN      Wisconsin     53538                  100.00   
1                NaN      Wisconsin     53538                  100.00   
2                NaN      Wisconsin     53538                  100.00   
3     Prairie Du Sac      Wisconsin     53578                   25.00   
4     Prairie Du Sac      Wisconsin     53578                   25.00   
...              ...            ...       ...                     ...   
5667             NaN      Wisconsin     53593                   52.01   
5668             NaN      Wisconsin     53593                   52.01   
5669         Seattle     Washington     98112                  100.00   
5670         Seattle     Washington     98112                  100.00   
5671         Madison      Wisconsin     53719                   51.96   

     Response.Time  Donation.Frequency Total.Donation.Amount  Donor_Score  \
0              NaN                   3                300.00    19.923984   
1              NaN                   3                300.00    19.923984   
2              NaN                   3                300.00    19.923984   
3         568673.0                   4                100.00    30.998648   
4              NaN                   4                100.00    30.998648   
...            ...                 ...                   ...          ...   
5667           NaN             

In [ ]:
import pandas as pd


# Create the 'Donor Kind' column
merged_df['Donor Kind'] = merged_df['Engagement Type'] + '-' + merged_df['Donation Type']

# Group by zip code and donor kind, count unique account IDs
donor_counts = merged_df.groupby(['Zip.Code', 'Donor Kind'])['Account.ID'].nunique().unstack(fill_value=0)

# Calculate the majority donor type and its percentage for each zip code
def majority_donor_type(row):
  max_value = row.max()
  if max_value == 0:
    return 'No Donors', 0  # Handle cases where there are no donors for a zip code
  majority_type = row.idxmax()
  percentage = (max_value / row.sum()) * 100
  return majority_type, percentage

majority_donors = donor_counts.apply(majority_donor_type, axis=1, result_type='expand')
majority_donors.columns = ['Majority Donor Type', 'Majority Donor Percentage']

# Concatenate the results
final_df = pd.concat([donor_counts, majority_donors], axis=1)

final_df

High Engagement-High Donation  High Engagement-Low Donation  \
Zip.Code                                                                
4                                     1                             0   
1801                                  0                             0   
2128                                  1                             0   
7901                                  1                             0   
10021                                 0                             0   
...                                 ...                           ...   
91942                                 1                             0   
92118                                 1                             0   
94941                                 0                             0   
95116                                 0                             0   
98112                                 1                             0   

          Low Engagement-High Donation  Low Engagement-Low Donation  \
Zip.Code                                                              
4                                    0                            0   
1801                                 1                            0   
2128                                 0                            0   
7901                                 0                            0   
10021                                1                            0   
...                                ...                          ...   
91942                                0                            0   
92118                                0                            0   
94941                                0                            1   
95116                                1                            0   
98112                                0                            0   

                    Majority Donor Type  Majority Donor Percentage  
Zip.Code                                                            
4         High Engagement-High Donation                      100.0  
1801       Low Engagement-High Donation                      100.0  
2128      High Engagement-High Donation                      100.0  
7901      High Engagement-High Donation                      100.0  
10021      Low Engagement-High Donation                      100.0  
...                                 ...                        ...  
91942     High Engagement-High Donation                      100.0  
92118     High Engagement-High Donation                      100.0  
94941       Low Engagement-Low Donation                      100.0  
95116      Low Engagement-High Donation                      100.0  
98112     High Engagement-High Donation                      100.0  

[253 rows x 6 columns]

In [ ]:

import pandas as pd


def prioritize_donor_kind(row):
    """Prioritizes donor kinds based on the given criteria."""
    donor_kinds = ['High Engagement-Low Donation', 'Low Engagement-High Donation', 'High Engagement-High Donation', 'Low Engagement-Low Donation']
    max_value = -1
    max_kind = ''
    for kind in donor_kinds:
        if kind in row.index:
            if row[kind] > max_value:
                max_value = row[kind]
                max_kind = kind
    return max_kind


# Apply the prioritization function to get the 'Prioritized Donor Kind' column
final_df['Prioritized Donor Kind'] = final_df.apply(prioritize_donor_kind, axis=1)

# Example usage: Displaying the final DataFrame
final_df

High Engagement-High Donation  High Engagement-Low Donation  \
Zip.Code                                                                
4                                     1                             0   
1801                                  0                             0   
2128                                  1                             0   
7901                                  1                             0   
10021                                 0                             0   
...                                 ...                           ...   
91942                                 1                             0   
92118                                 1                             0   
94941                                 0                             0   
95116                                 0                             0   
98112                                 1                             0   

          Low Engagement-High Donation  Low Engagement-Low Donation  \
Zip.Code                                                              
4                                    0                            0   
1801                                 1                            0   
2128                                 0                            0   
7901                                 0                            0   
10021                                1                            0   
...                                ...                          ...   
91942                                0                            0   
92118                                0                            0   
94941                                0                            1   
95116                                1                            0   
98112                                0                            0   

                    Majority Donor Type  Majority Donor Percentage  \
Zip.Code                                                             
4         High Engagement-High Donation                      100.0   
1801       Low Engagement-High Donation                      100.0   
2128      High Engagement-High Donation                      100.0   
7901      High Engagement-High Donation                      100.0   
10021      Low Engagement-High Donation                      100.0   
...                                 ...                        ...   
91942     High Engagement-High Donation                      100.0   
92118     High Engagement-High Donation                      100.0   
94941       Low Engagement-Low Donation                      100.0   
95116      Low Engagement-High Donation                      100.0   
98112     High Engagement-High Donation                      100.0   

                 Prioritized Donor Kind  
Zip.Code                                 
4         High Engagement-High Donation  
1801       Low Engagement-High Donation  
2128      High Engagement-High Donation  
7901      High Engagement-High Donation  
10021      Low Engagement-High Donation  
...                                 ...  
91942     High Engagement-High Donation  
92118     High Engagement-High Donation  
94941       Low Engagement-Low Donation  
95116      Low Engagement-High Donation  
98112     High Engagement-High Donation  

[253 rows x 7 columns]

In [49]:
final_df = final_df.reset_index()

# Add a new index with serial numbers
final_df.index = range(len(final_df))

final_df

Zip.Code  High Engagement-High Donation  High Engagement-Low Donation  \
0           4                              1                             0   
1        1801                              0                             0   
2        2128                              1                             0   
3        7901                              1                             0   
4       10021                              0                             0   
..        ...                            ...                           ...   
248     91942                              1                             0   
249     92118                              1                             0   
250     94941                              0                             0   
251     95116                              0                             0   
252     98112                              1                             0   

     Low Engagement-High Donation  Low Engagement-Low Donation  \
0                               0                            0   
1                               1                            0   
2                               0                            0   
3                               0                            0   
4                               1                            0   
..                            ...                          ...   
248                             0                            0   
249                             0                            0   
250                             0                            1   
251                             1                            0   
252                             0                            0   

               Majority Donor Type  Majority Donor Percentage  \
0    High Engagement-High Donation                      100.0   
1     Low Engagement-High Donation                      100.0   
2    High Engagement-High Donation                      100.0   
3    High Engagement-High Donation                      100.0   
4     Low Engagement-High Donation                      100.0   
..                             ...                        ...   
248  High Engagement-High Donation                      100.0   
249  High Engagement-High Donation                      100.0   
250    Low Engagement-Low Donation                      100.0   
251   Low Engagement-High Donation                      100.0   
252  High Engagement-High Donation                      100.0   

            Prioritized Donor Kind  
0    High Engagement-High Donation  
1     Low Engagement-High Donation  
2    High Engagement-High Donation  
3    High Engagement-High Donation  
4     Low Engagement-High Donation  
..                             ...  
248  High Engagement-High Donation  
249  High Engagement-High Donation  
250    Low Engagement-Low Donation  
251   Low Engagement-High Donation  
252  High Engagement-High Donation  

[253 rows x 8 columns]

In [ ]:
# Merge the DataFrames on 'Zip.Code'
result_df = pd.merge(merged_df, final_df[['Zip.Code', 'Prioritized Donor Kind', 'Majority Donor Percentage']], on='Zip.Code', how='left')

result_df

Unnamed: 0  Account.ID Email.First.Open.Date Email.Last.Open.Date  \
0              0           8                   NaN                  NaN   
1              1           8                   NaN                  NaN   
2              2           8            2022-08-18           2022-08-18   
3              3           9            2021-05-03           2021-06-01   
4              4           9                   NaN                  NaN   
...          ...         ...                   ...                  ...   
5667        5696        5863                   NaN                  NaN   
5668        5697        5863                   NaN                  NaN   
5669        5698        5867                   NaN                  NaN   
5670        5699        5867                   NaN                  NaN   
5671        5700        7099                   NaN                  NaN   

      Open.Count Email.Recipient.Full.Name                  Email  \
0            NaN            Peggy Stebbins   tyandpeggy@gmail.com   
1            NaN            Peggy Stebbins   tyandpeggy@gmail.com   
2            1.0            Peggy Stebbins   tyandpeggy@gmail.com   
3           26.0            Samantha Maier  Sglass32085@gmail.com   
4            NaN            Samantha Maier  Sglass32085@gmail.com   
...          ...                       ...                    ...   
5667         NaN                 Caleb Cox    cjcox.byu@gmail.com   
5668         NaN                 Caleb Cox    cjcox.byu@gmail.com   
5669         NaN    Ken and Lnn Cunningham           ken@kwc1.net   
5670         NaN   Ken and Lynn Cunningham           ken@kwc1.net   
5671         NaN              Julie Wilson       office@umcmh.org   

      Email.Retry.Count Email.Send.Date.Time      Email.Type  ...  \
0                   2.0  2020-09-23 08:15:52  Campaign Email  ...   
1                   2.0  2021-05-03 10:02:19  Campaign Email  ...   
2                   NaN  2022-08-18 06:30:54  Campaign Email  ...   
3                   2.0  2021-05-03 10:02:07  Campaign Email  ...   
4                   2.0  2020-09-23 08:15:45  Campaign Email  ...   
...                 ...                  ...             ...  ...   
5667                2.0  2021-05-03 10:02:37  Campaign Email  ...   
5668                2.0  2020-09-23 08:15:53  Campaign Email  ...   
5669                2.0  2021-05-03 10:03:04  Campaign Email  ...   
5670                NaN  2022-08-18 06:31:00  Campaign Email  ...   
5671                NaN  2022-08-18 06:30:54  Campaign Email  ...   

     Largest.Donation.Amount Response.Time  Donation.Frequency  \
0                     100.00           NaN                   3   
1                     100.00           NaN                   3   
2                     100.00           NaN                   3   
3                      25.00      568673.0                   4   
4                      25.00           NaN                   4   
...                      ...           ...                 ...   
5667                   52.01           NaN                   3   
5668                   52.01           NaN                   3   
5669                  100.00           NaN                   2   
5670                  100.00           NaN                   2   
5671                   51.96           NaN                   1   

     Total.Donation.Amount Donor_Score  Engagement Type  Donation Type  \
0                   300.00   19.923984  High Engagement  High Donation   
1                   300.00   19.923984  High Engagement  High Donation   
2                   300.00   19.923984  High Engagement  High Donation   
3                   100.00   30.998648  High Engagement  High Donation   
4                   100.00   30.998648  High Engagement  High Donation   
...                    ...         ...              ...            ...   
5667                156.03   22.669674  High Engagement  High Donation   
5668                156.03   22.669674  High Engagement  High 

In [51]:
result_df = result_df.drop(columns=['Donor Kind'])

In [ ]:
result_df.to_csv('results_df.csv')

In [54]:
zip_code_counts = result_df.groupby('Prioritized Donor Kind')['Zip.Code'].nunique()

# Calculate percentages
total_zip_codes = zip_code_counts.sum()
zip_code_percentages = (zip_code_counts / total_zip_codes) * 100

# Create a DataFrame for the results
zip_code_summary = pd.DataFrame({
    'Unique Zip Code Count': zip_code_counts,
    'Percentage': zip_code_percentages
})

zip_code_summary

Unique Zip Code Count  Percentage
Prioritized Donor Kind                                          
High Engagement-High Donation                    109   43.083004
High Engagement-Low Donation                      84   33.201581
Low Engagement-High Donation                      22    8.695652
Low Engagement-Low Donation                       38   15.019763